In [1]:
import os.path as osp
import sys
path = osp.dirname(osp.abspath(''))
sys.path.append(path)
sys.path.append(osp.join(path, "open_biomed"))
path

'/mnt/users/zhaosy/home/Open_DAIR_BioMed'

In [8]:
from dataset.ctc_dataset import Baron
import json
from torch.utils.data import DataLoader

config = json.load(open("../configs/ctc/cellLM.json", "r"))
dataset = Baron(path="../datasets/ctc/",
              config=config["data"], seed=2023)
loader = DataLoader(dataset, batch_size=128, shuffle=False)

/mnt/users/zhaosy/miniconda3/lib/python3.9/site-packages/anndata/_core/anndata.py:1838: UserWarning: Observation names are not unique. To make them unique, call `.obs_names_make_unique`.
  utils.warn_names_duplicates("obs")


In [9]:
from models.task_model.ctc_model import CTCModel
import torch
model = CTCModel(config["network"], dataset.num_classes)
model.load_state_dict(torch.load("../ckpts/finetune_ckpts/celllm_finetune.pth")["model_state_dict"])


<All keys matched successfully>

In [12]:
from tqdm import tqdm
import torch.nn as nn
from sklearn.metrics import accuracy_score, f1_score
with torch.no_grad():
    model.cuda(1)
    model.eval()
    all_preds, all_y = [], []
    for cell, label in tqdm(loader):
        cell= cell.cuda(1)
        logits = model(cell)
        pred = nn.Softmax(dim=-1)(logits).argmax(dim=-1).detach().cpu()
        # pred[np.amax(np.array(pred), axis=-1) < args.unassign_threshold] = -1

        all_preds.append(pred)
        all_y.append(label)
    
    all_preds = torch.cat(all_preds, dim=0)
    all_y = torch.cat(all_y, dim=0)
    # for i in range(20):
    #     print(all_preds[i].item(), all_y[i].item())
    print( {
        "Accuracy": accuracy_score(all_preds, all_y),
        "macro F1 Score": f1_score(all_preds, all_y, average='macro'),
        "weighted F1 Score": f1_score(all_preds, all_y, average='weighted'),
    } )

100%|██████████| 67/67 [10:02<00:00,  8.99s/it]

{'Accuracy': 0.9968491072470533, 'macro F1 Score': 0.9821247321224725, 'weighted F1 Score': 0.9968824031654996}


In [13]:
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
import numpy as np
import torch
cell_emb = torch.cat(dataset.cells).view(len(dataset.cells), -1).numpy()
label = dataset.labels
tsne = TSNE(n_components=2, init='pca', random_state=501)
pca_emb = tsne.fit_transform(cell_emb)


In [14]:
import matplotlib.pyplot as plt
plt.rcParams['figure.dpi'] = 1080 
# plt.rcParams['figure.figsize'] = (2, 1) 
fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(20, 5))
for l in range(11):
    x = [i[0] for i in pca_emb[label == l]]
    y = [i[1] for i in pca_emb[label == l]]
    # z = [i[2] for i in pca_emb[label == l]]
    ax1.scatter(x, y, s=0.5)
    ax1.set_title('Ground truth')

    x = [i[0] for i in pca_emb[all_preds == l]]
    y = [i[1] for i in pca_emb[all_preds == l]]
    # z = [i[2] for i in pca_emb[label == l]]
    ax2.scatter(x, y, s=0.5)
    ax2.set_title('Finetuned CellLM prediction')